
# Calculation average house property price in different Moscow districts depending on venues in a district 

## PART I:  <font size="4"> <b> Problem defenition and data preparation </b> </font>

<sup> *The capstone project of IBM Data Science Professional Certificate Specialization* </sup>


### Business problem defining

*Moscow (Russia) is in the top-20 cities with most expensive property prices in the world. Locals jokes that prices in Russia never decrease. They rise due to economic growth and even due to economic drawdown. Real-estate prices were rising during economic growth in Russia and peaked 6000 USD (or 150 000 RUB) per sq.meter on average in 2008. They were also rising in local currency due to inflation in Russia recent years when market oil price fell.*


![](https://www.irn.ru/graph/services/classes2.php?class=all&type=1&period=0&step=mon&grnum=1&currency=1)
<div style="text-align:center"> <sup><b>image:</b> house property price index (USD/sq meter from 2000 year)</sup></div>
<div style="text-align:center"> <sup><b>source:</b> www.irn.ru</sup></div>
  
![](https://www.irn.ru/graph/services/classes2.php?class=all&type=1&period=0&step=mon&grnum=1&currency=0)
<div style="text-align:center"> <sup><b>image:</b> house property price index (RUB/sq meter from 2000 year)</sup></div>
<div style="text-align:center"> <sup><b>source:</b> www.irn.ru</sup></div>


*Within the project, I'd like to consider the following potential situation. Imagine a construction company is going to lanch a project of affordable housing not far away from Moscow and build new houses. So they need to estimate what the market price for their real-estate will be within the market. Let's assume they are going to build new houses in the town called Mytischi located in 22.9 km from Moscow city center. At the same time we have to use FourSquare API to solve the problem because FourSquare data using is must as it is discribed as main condition of capstone project (everything else is the student chooses).*

**Summing up we need to calculate the final consumer price in USD per sq.meter for house property in Mytischi town using FourSquare API**

### Data description to be used

- [.geojson file with polygons of each Moscow neighborhood submitted by **codeforamerica** on github](https://github.com/codeforamerica/click_that_hood/blob/master/public/data/moscow.geojson)
- [the full list of Moscow neighborhoods with it's administrative devision from **gis-lab**](http://gis-lab.info/qa/moscow-atd.html)
- [average price per sq. meter in each Moscow neighborhood from **realtor-pro**](https://www.realtor-pro.ru/stoimost-kvadratnogo-metra-zhilya-v-moskve-po-rayonam)
- Amount of venues of each [venue category from FourSquare](https://developer.foursquare.com/docs/resources/categories) located in radius of 2 km of each polygon's centroid belonged to specific Moscow neighborhood


### Code section:

Importing libraries

In [93]:
import pandas as pd
import numpy as np
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

from geopy.geocoders import Nominatim
import folium # map rendering library

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors


import json
import requests # library to handle requests
import branca

Defining a function we will use to calculatuin a centroid of each polygon

In [94]:
def centroid(vertexes):
     x_list = [vertex [0] for vertex in vertexes]
     y_list = [vertex [1] for vertex in vertexes]
     leng = len(vertexes)
     x = sum(x_list) / leng
     y = sum(y_list) / leng
     return(x, y)

Data from https://raw.githubusercontent.com/codeforamerica/click_that_hood/master/public/data/moscow.geojson

In [95]:
moscow_geo=r'C:\Users\Maxim.Hanin\moscow.geojson' # geojson file
with open(moscow_geo) as f:
    data = json.load(f)

Filling the main dataframe

In [96]:
raw_datalist=[]
for i in range(len(data['features'])):
    raw_datalist.append([data['features'][i]['properties']['name'], 
                       data['features'][i]['properties']['name_lat'],                                      
                       centroid(data['features'][i]['geometry']['coordinates'][0][0])[1],
                        centroid(data['features'][i]['geometry']['coordinates'][0][0])[0]])
df=pd.DataFrame(raw_datalist)
df.columns=['District name(ru)', 'District name(en)','Lat','Lng']
print('Number of districts =', df.shape[0])
df.head(3)

Number of districts = 125


District name(ru)   District name(en)        Lat        Lng
0    район Восточный    rajon Vostochnyj  55.814862  37.874472
1  Обручевский район  Obruchevskij rajon  55.660381  37.523142
2     район Свиблово      rajon Sviblovo  55.855174  37.644165

Getting the data about Moscow administrative devision. Table #3

In [97]:
msc_regions=pd.read_html('http://gis-lab.info/qa/moscow-atd.html')[3]

More information about administrative devision in Moscow you can find in wiki (https://en.wikipedia.org/wiki/Administrative_divisions_of_Moscow)

In [98]:
msc_regions = msc_regions.drop([0,4,5], axis=1)
msc_regions.columns = ['Districts', 'Okrugs', 'Type']
msc_regions = msc_regions.drop([0], axis=0).reset_index(drop=True)
msc_regions.head(3)

Districts Okrugs                 Type
0  Академический   ЮЗАО  Муниципальный округ
1   Алексеевский   СВАО  Муниципальный округ
2   Алтуфьевский   СВАО  Муниципальный округ

For table merging from different souces I created a new column called 'Districts' to use it as a key for each table

In [99]:
df['Districts']=df['District name(ru)'].str.replace('район', '').str.strip()
df.head(3)

District name(ru)   District name(en)        Lat        Lng    Districts
0    район Восточный    rajon Vostochnyj  55.814862  37.874472    Восточный
1  Обручевский район  Obruchevskij rajon  55.660381  37.523142  Обручевский
2     район Свиблово      rajon Sviblovo  55.855174  37.644165     Свиблово

Two tables merging to see administrative devisions called 'Okrugs'

In [100]:
df=df.merge(msc_regions, how='inner', on='Districts', copy=False)
print('Number of districts =', df.shape[0])
df.head(3)

Number of districts = 125


District name(ru)   District name(en)        Lat        Lng    Districts  \
0    район Восточный    rajon Vostochnyj  55.814862  37.874472    Восточный   
1  Обручевский район  Obruchevskij rajon  55.660381  37.523142  Обручевский   
2     район Свиблово      rajon Sviblovo  55.855174  37.644165     Свиблово   

  Okrugs                 Type  
0    ВАО  Муниципальный округ  
1   ЮЗАО  Муниципальный округ  
2   СВАО  Муниципальный округ

Calculating how many districts in different Okrugs to see whether everything is done well there

In [101]:
df['Okrugs_lbl'] = df['Okrugs'].astype("category").cat.codes
df['Okrugs_lbl'].value_counts()

4    17
7    16
3    16
0    16
1    13
9    12
8    12
6    10
5     8
2     5
Name: Okrugs_lbl, dtype: int64

Web scrapping of our third table to add price per sq. meter for each neighborhood:

In [102]:
Prices = pd.read_html('https://www.realtor-pro.ru/stoimost-kvadratnogo-metra-zhilya-v-moskve-po-rayonam')[0]
Prices.head(3)

Рейтинг районов и метро  по уровню цен на Сентябрь 2018 г. (www.irn.ru)  \
                                                                        №   
0                                                  1                        
1                                                  2                        
2                                                  3                        

  Unnamed: 1_level_0                                 Unnamed: 2_level_0  \
              Районы                                      Станции метро   
0        Китай-город  Китай-город, Кузнецкий мост, Лубянка, Охотный ...   
1          Остоженка                       Кропоткинская, Парк культуры   
2           Тверской        Маяковская, Пушкинская, Тверская, Чеховская   

  Unnamed: 3_level_0 Unnamed: 4_level_0  
         РУБ за кв.м        USD за кв.м  
0            399 539               5899  
1            392 360               5793  
2            350 029               5168

Data wrangling and preparation for merging with the main dataframe 

In [103]:
Prices.columns=Prices.columns.droplevel()
Prices=Prices.drop(['№', 'Станции метро', 'РУБ за кв.м'], axis=1)
Prices.columns=['Districts', 'USD per sq.meter']
Prices.head(3)

Districts  USD per sq.meter
0  Китай-город              5899
1    Остоженка              5793
2     Тверской              5168

In [104]:
Prices.tail(3)

Districts  USD per sq.meter
83                                       Южное Бутово              1727
84              Бирюлево Восточное, Бирюлево Западное              1641
85  Крюково, Матушкино, Савёлки, Силино, Старое Кр...              1486

Looks like in the table we have several neighborhoods separated by comma with the same prices (table is grouped by price) so we need to split it in a way each row reffers to one specific district and it's price

In [105]:
Prices = Prices.set_index(['USD per sq.meter']).stack().str.split(',', expand=True).stack().unstack(-2).reset_index(-1, drop=True).reset_index()
Prices['Districts']=Prices['Districts'].str.strip()
Prices.tail(3)

USD per sq.meter       Districts
126              1486         Савёлки
127              1486          Силино
128              1486  Старое Крюково

Preparing our main column-key 'Districts' for merging. Wrangling again...

In [106]:
Prices['Districts']=Prices['Districts'].str.replace('ё', 'е')
df['Districts']=df['Districts'].str.replace('ё', 'е')
Prices['Districts']=Prices['Districts'].str.lower()
df['Districts']=df['Districts'].str.lower()

Join it with main DF

In [107]:
df=df.merge(Prices, how='inner', on='Districts', copy=True)
print('Number of districts =', df.shape[0])
df.head(3)

Number of districts = 125


District name(ru)   District name(en)        Lat        Lng    Districts  \
0    район Восточный    rajon Vostochnyj  55.814862  37.874472    восточный   
1  Обручевский район  Obruchevskij rajon  55.660381  37.523142  обручевский   
2     район Свиблово      rajon Sviblovo  55.855174  37.644165     свиблово   

  Okrugs                 Type  Okrugs_lbl  USD per sq.meter  
0    ВАО  Муниципальный округ           0              1886  
1   ЮЗАО  Муниципальный округ           9              2982  
2   СВАО  Муниципальный округ           4              2558

Now lets see what we have by creating a map of Moscow to see all scope of work. We are going to define each Okrug with specific color for better understanding further in which Okrug prices are higher

Firstly Lets' know coordinates of Moscow using Nominatim

In [108]:
Moscow = 'Moscow'
geolocator = Nominatim()
msc_location = geolocator.geocode(Moscow)
msc_latitude = msc_location.latitude
msc_longitude = msc_location.longitude

H:\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  


And define coordinates where our new house will be built

In [109]:
Mytischi_Lat=55.914603
Mytischi_Lng=37.731570

In [110]:

moscow_map = folium.Map(location=[msc_latitude, msc_longitude], zoom_start=9,tiles='Stamen Toner')

polygonstyle_function = lambda feature: dict(opacity=0.0, fill_opacity=0.0, line_opacity=0.0)

x = np.arange(df['Okrugs_lbl'].nunique())
ys = [i+x+(i*x)**2 for i in range(df['Okrugs_lbl'].nunique())]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

for i in range(len(data['features'])):


    moscow_map.choropleth(
        geo_data=data['features'][i]['geometry'],
        key_on='feature.properties',
        fill_color=rainbow[df.loc[i, 'Okrugs_lbl']-1], 
        fill_opacity=0.3, 
        line_opacity=0.4,
        legend_name='Moscow Districts')   
    
    geojson = folium.GeoJson(data['features'][i]['geometry'], style_function=polygonstyle_function)
    popup =folium.Popup('{} : {} / {}. Price per sq.meter = {} USD'.format(df.loc[i, 'Okrugs'], 
                                                               df.loc[i, 'District name(ru)'], 
                                                               df.loc[i, 'District name(en)'],
                                                               df.loc[i, 'USD per sq.meter']))
    popup.add_to(geojson)
    geojson.add_to(moscow_map)
    
    folium.CircleMarker(
        [df.loc[i, 'Lat'], df.loc[i, 'Lng']],
        radius=3,
        weight=0.5,
        popup='{} : {} / {}. Price per sq.meter = {} USD'.format(df.loc[i, 'Okrugs'], 
                                      df.loc[i, 'District name(ru)'], 
                                      df.loc[i, 'District name(en)'],
                                      df.loc[i, 'USD per sq.meter']),
        color='black',
        fill=True,
        fill_color=rainbow[df.loc[i, 'Okrugs_lbl']-1],
        fill_opacity=1).add_to(moscow_map)

folium.Marker([Mytischi_Lat, Mytischi_Lng],  icon=folium.Icon(color='red', icon='home'), popup='Мытищи / Mytischi. Targer neigborhood and 2 km radius').add_to(moscow_map)
folium.Circle([Mytischi_Lat, Mytischi_Lng], 2000, color='red').add_to(moscow_map)
    
moscow_map

H:\Anaconda3\lib\site-packages\folium\folium.py:432: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


Now I do the same map with the same neighborhoods recolor them with gradient from red to green depending on housing price in USD/per sq. meter in each neighborhood

In [111]:
colormap = branca.colormap.LinearColormap(colors=['green', 'yellow', 'red'], 
                                          index=[min(df['USD per sq.meter']), 3000, max(df['USD per sq.meter'])],
                                          vmin=min(df['USD per sq.meter']),vmax=max(df['USD per sq.meter']))
colormap.caption = "The cost of housing in different parts of Moscow (USD per sq.meter)"
# create a plain world map
moscow_map = folium.Map(location=[msc_latitude, msc_longitude], zoom_start=9, tiles='Stamen Toner')

polygonstyle_function = lambda feature: dict(opacity=0.0, fillColor='', fill_opacity=0.0, line_opacity=0.0)

for i in range(len(data['features'])):

    moscow_map.choropleth(
        geo_data=data['features'][i]['geometry'],
        key_on='feature.properties',
        fill_color=colormap(df.loc[i, 'USD per sq.meter']), 
        fill_opacity=0.4, 
        line_opacity=0.3
        )  

    geojson = folium.GeoJson(data['features'][i]['geometry'], style_function=polygonstyle_function)
    popup =folium.Popup('{} : {} / {}. Price per sq.meter = {} USD'.format(df.loc[i, 'Okrugs'], 
                                                               df.loc[i, 'District name(ru)'], 
                                                               df.loc[i, 'District name(en)'],
                                                               df.loc[i, 'USD per sq.meter']))
    popup.add_to(geojson)
    geojson.add_to(moscow_map)
    
for i in range(len(df['Districts'])):
    
    folium.CircleMarker(
        [df.loc[i, 'Lat'], df.loc[i, 'Lng']],
        radius=3,
        weight=0.5,
        popup='{} : {} / {}. Price per sq.meter = {} USD'.format(df.loc[i, 'Okrugs'], 
                                      df.loc[i, 'District name(ru)'], 
                                      df.loc[i, 'District name(en)'],
                                      df.loc[i, 'USD per sq.meter']),
        color='black',
        fill=True,
        fill_color=colormap(df.loc[i, 'USD per sq.meter']),
        fill_opacity=1).add_to(moscow_map)
    
folium.Marker([Mytischi_Lat, Mytischi_Lng],  icon=folium.Icon(color='red', icon='home'), popup='Мытищи / Mytischi. Targer neigborhood and 2 km radius').add_to(moscow_map)
folium.Circle([Mytischi_Lat, Mytischi_Lng], 2000, color='red').add_to(moscow_map)
    

colormap.add_to(moscow_map)    
moscow_map

H:\Anaconda3\lib\site-packages\folium\folium.py:432: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


Now it is time to collect data FourSqure using it's API. We're going to use amount of venues of each category in a neigborhood as features in our model in part 2. Here we should define credential for our API access but for known reason I've hided them for you. Sry

In [143]:
CLIENT_ID = '*' # your Foursquare ID
CLIENT_SECRET = '*' # your Foursquare Secret
VERSION = '20180604'
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: *
CLIENT_SECRET:*


First, we should know how many and what kind of venue categories FourSquare has. So we make a query to get a response

In [114]:
url='https://api.foursquare.com/v2/venues/categories?client_id={}&client_secret={}&v={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION) 
response=requests.get(url).json()

It looks like there categories which has subcateries and some of them has subsubcategories etc. So here it is decided to use only 2nd level of cetegories. It should be enough

In [125]:
len(response['response']['categories'])
print("There're "+ str(len(response['response']['categories'])) +" categories of 1st level (major categories)")

There're 10 categoris of 1st level (major categories)


Creating a dataframe from categories of first level from returned .json file

In [126]:
cats=[]
for cat in response['response']['categories']:
    for sub_cat in cat['categories']:
        cats.append([cat['name'], sub_cat['name'], sub_cat['id']])
df_cats=pd.DataFrame(cats, columns=['Category', 'Subcategory', 'ID'])

So now let's see how many features (2nd level cetegories) our model will have

In [132]:
print("There're "+ str(df_cats.shape[0]) +" categories of 2nd level)")

There're 456 categories of 2nd level)


Should be enough

In the next code cells there is an algoritm sending a search query to FourSqure about location and name of each venue in 2 kilimeters radius of a polygon centroid reffering to a neigborhood. 

With 456 categories and 125 neigborhoods we must send a query to FourSqure 57 000 times. It took from me more than 4 hours in total to fill my final dataframe I will work with.

Sometimes it returned error (because of the internet connection) so the cell was relunched several times to fill null cells.

In [139]:
FQ_df=[]

In [ ]:
for i in range(len(df['Districts'])):
            
            print(df.loc[i, 'Districts'])
            
            for each in range(len(df_cats)):
          
                venuetype_id = df_cats.loc[each, 'ID']
                venuetype_name = df_cats.loc[each, 'Subcategory']
                print(df_cats.loc[each, 'Category'], df_cats.loc[each, 'Subcategory'])
                
#                if(np.isnan(df.loc[i, venuetype_name])): #uncomment to fill null values only (to restore the process after returning a error)

                url='https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&intent={}&categoryId={}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, df.loc[i, 'Lat'], df.loc[i, 'Lng'], 'browse', venuetype_id, VERSION, 2000, 50)
                fq_data=requests.get(url).json()
                
                try:
                        df.loc[i, venuetype_name]=len(fq_data['response']['venues'])
                
                        for each in fq_data['response']['venues']:
              
                          print({'cat_name':each['categories'][0]['name'], 'name':each['name']})
                
                          FQ_df.append([df.loc[i, 'Districts'], 
                                        venuetype_name,
                                        each['id'], 
                                        each['categories'][0]['name'], 
                                        each['name'], 
                                        each['location']['lat'], 
                                        each['location']['lng']])
                except:    
                        df.loc[i, venuetype_name]=0
#                else:
#                    print(i, df.loc[i, 'Districts'], 'is already filled')                        

In [142]:
df_venues=pd.DataFrame(FQ_df, columns=['Districts', 'Venue cat', 'Venue ID', 'Venue type', 'Venue name', 'Lat', 'Lng'])
df_venues.head(3)

Districts              Venue cat                  Venue ID  \
0  восточный  General Entertainment  50f7fe0fe4b0961be043f1a5   
1  восточный  General Entertainment  51fa197a454ac4e03e99e44c   
2  восточный  General Entertainment  4f74bc8ce4b07e696393b034   

              Venue type                  Venue name        Lat        Lng  
0  General Entertainment  Детский центр " Смышлёныш"  55.820919  37.877037  
1  Performing Arts Venue                 ДК «Восток»  55.819710  37.858237  
2  General Entertainment                  ДДЦ "Ежик"  55.823444  37.877469

Saving progress for part II

In [ ]:
df_venues.to_csv(r'D:\venuedataset.csv', encoding='utf-8-sig')
df.to_csv(r'D:\dataset_main.csv', encoding='utf-8-sig')